In [1]:
#load in dependencies
import pandas as pd
import numpy as np
import bz2
import json

In [2]:
#this needs to be optimized better for reading larger files
#consider splitting by }{ to exclude entries like {...{...}|...}|{...}|
#above gave error: IOPub data rate exceeded.  apparently .split doesn't like to parse on multiple characters
#might be able to pull something off with a regex or a location/splice loop

#files are saved by month and year as a list of JSON's compressed into a bz2 file
#for memory saving purposes I ran this for each year separately
years = ["2011"]
#years = ["2006", "2007", "2008", "2009", "2010", "2011"]
months = ["01", "02", "03", "04", "05", "06", "07", "08", "09", "10", "11", "12"]
targets = ['ps2', 'ps3', 'ps4', 'ps5', 'playstation', 'xbox'] #list of desired mentions
post_list = []

for y in years:
    for m in months:
        try:
            filename = "data/" + y + "/RC_" + y + "-" + m + ".bz2"
            with bz2.open(filename, 'rb') as file:
                str_file = file.read().decode('ascii')
                parsed_file = str_file.split("}")
                for post in parsed_file:
                    post += "}"
                    if any(x in post for x in targets): #looks for console mentions
                        post_tuple = [post, y, m]
                        post_list.append(post_tuple)
                
            print(filename + " parsed")
            
        except:
            print("file named " + filename + " does not exist")
    print(len(post_list))

data/2011/RC_2011-01.bz2 parsed
data/2011/RC_2011-02.bz2 parsed
data/2011/RC_2011-03.bz2 parsed
data/2011/RC_2011-04.bz2 parsed
data/2011/RC_2011-05.bz2 parsed
file named data/2011/RC_2011-06.bz2 does not exist
file named data/2011/RC_2011-07.bz2 does not exist
file named data/2011/RC_2011-08.bz2 does not exist
file named data/2011/RC_2011-09.bz2 does not exist
file named data/2011/RC_2011-10.bz2 does not exist
file named data/2011/RC_2011-11.bz2 does not exist
file named data/2011/RC_2011-12.bz2 does not exist
82636


In [3]:
#check out layout of each post
print(post_list[0])

['\n{"author":"alphazero924","subreddit_id":"t5_2qhk2","score":4,"name":"t1_c1b06l4","author_flair_text":null,"subreddit":"xbox360","controversiality":0,"created_utc":"1293840094","parent_id":"t1_c1azy3p","retrieved_on":1426664472,"edited":false,"gilded":0,"distinguished":null,"ups":4,"body":"Nice try, Microsoft representative.","author_flair_css_class":null,"id":"c1b06l4","score_hidden":false,"link_id":"t3_eu6z1","downs":0,"archived":true}', '2011', '01']


In [4]:
#convert all fitting strings to jsons
ps_json_list = []
xbox_json_list = []
blacklist = ['Fluxbox', 'fluxbox', 'ps2pdf', 'cps3', 'mps3', 'Trixbox', 'rps25', 'aps2', 'gps2', 'lps3', 'pps25'] 
#string similar to desired results but for wrong topics

for post, year, month in post_list:#puts xbox and ps mentions into database
    try:
        x = json.loads(post)
        if any(topic in x['body'] for topic in ['xbox']):#check for xbox mentions
            if not any(item in x['body'] for item in blacklist):
                json_tuple = [x, year, month]
                xbox_json_list.append(json_tuple)

        if any(topic in x['body'] for topic in ['ps2', 'ps3', 'ps4', 'ps5', 'playstation']):#check for playstation mentions
            if not any(item in x['body'] for item in blacklist):
                json_tuple = [x, year, month]
                ps_json_list.append(json_tuple)

    except:           #main errors I've noticed so far include posts that contain '}'
        print("Error on " + post)
        print()
        
for post, year, month in xbox_json_list:#check what kind of data shows up to develop blacklist
    print(post['subreddit'], post['body'])
    print('///////////////////////////////////////////////////////////////')
for post, year, month in ps_json_list:
    print(post['subreddit'], post['body'])
    print('///////////////////////////////////////////////////////////////')

Error on 
{"author_flair_text":"as above so below","created_utc":"1294289155","name":"t1_c1bltsd","id":"c1bltsd","score":2,"author_flair_css_class":"flair-other","downs":0,"ups":2,"subreddit_id":"t5_2qhk2","author":"apothekari","archived":true,"score_hidden":false,"parent_id":"t3_ewz37","retrieved_on":1426674676,"edited":false,"controversiality":0,"gilded":0,"subreddit":"xbox360","body":"There's a moment where the XBOX and the TV have to sort of check in w/each other due to the HDCP protocol{fancy anagram for HDMI's official DRM bullshit}

Error on 
{"id":"c1dps3w","subreddit":"netsec","author_flair_text":null,"subreddit_id":"t5_1rqwi","edited":false,"link_id":"t3_f6rkr","score_hidden":false,"name":"t1_c1dps3w","author":"lookouttacks","score":10,"created_utc":"1295662977","controversiality":0,"archived":true,"author_flair_css_class":null,"gilded":0,"distinguished":null,"downs":0,"retrieved_on":1426710680,"body":"Don't let users enter something that will be output as javascript code?\n\

Error on 
{"ups":38,"downs":0,"id":"c1k3oy6","archived":true,"gilded":0,"parent_id":"t1_c1k3n1t","score_hidden":false,"name":"t1_c1k3oy6","link_id":"t3_g0ty2","author_flair_css_class":null,"body":"I think console releases are going to slow down even more as the years go one.  The xbox 720 (or whatever) will probably not be replaced for a decade, and then the 1080 will live on for two decades.  Eventually graphics on a monitor or tv will get so good there will be no reason to upgrade the graphics engine.  At this point I think the world will start shifting to immersion.  Things like the kinect and the wii will become better and better, people will be looking towards virtual reality for the next gamming jump.  We will demand feed back in our games and then will start plugging ourselves into the matrix.  I wonder if I will live to see that kind of technology, I really hope so.  By then games won't just be games anymore, there will be some network that we plug ourselves into for movies, li

Favors I have a rockband guitar for xbox 360 I no longer use and this looks like an interesting investment PM me your details and we shall converse.
///////////////////////////////////////////////////////////////
AskReddit I agree with this, but i do hear their customer service is great. If i wanted to pay for only parts i would, but seeing how im only going to be able to get one last laptop out of my parents before im cut off for good, i want to make sure that if my hard drive fails, ill be able to get a new one under warranty. without spending an hour on the phone with somebody who spells my name "E-for Elephant, R-for rice, I-as in india, C, for cook." (true story. 1800-4my-xbox.) 
But, if asus or lenovo do have great customer service im all ears. Or if you have an opnion on system 76 i would love to hear it too. off topic thread with the OP, ftw.
///////////////////////////////////////////////////////////////
gaming My uncle bought a samsung un55c6500 and has absolutely no use for 

AskReddit If you only want to game, xbox is the way to go.

I have a PS3, and I enjoy the media center-ness of the unit, but to each his own.
///////////////////////////////////////////////////////////////
AskReddit PS3 and Xbox 360 have almost identical graphics as most games are ports so don't choose based on that.  Pick whatever your friends play really, I like xbox's lineup of games better and I hate the PS3 controls, but thats just me.  
///////////////////////////////////////////////////////////////
AskReddit I have a ps3, and in addition to games I stream videos and music to it from the pc in my other room using PS3MediaServer. I don't know if xbox has something similar (probably) but because the ps3 comes with a built-in blu-ray player I'd say it's a better all-around investment.
///////////////////////////////////////////////////////////////
xbox360 The day the dlc came out it didn't work for me until the the game got a title update the next day. Connect to xbox live and then 

WTF A coffee slut drinks nothing but coffee, a xbox slut does nothing but play xbox, I think she just bangs Barons. 
///////////////////////////////////////////////////////////////
gaming Of course i should care. If someone is in the position i am
which i cant not afford a PS3 well guess what I am missing
some of the best games out of last decade. Uncharted, LBP, 
God of War, hell i even loved the Ratchet games in the ps2.

It is not a flame war it is reasonable for anyone without both consoles
to care about exclusives in his console and in the other consoles. And for real
most AAA games exclusive to the xbox have being second party games
or time exclusive, so yeah MS have forgot about making quality games on their own.
///////////////////////////////////////////////////////////////
gaming Xbox games, probably not. That would require emulating an xbox on the ps3, and I don't think even the ps3 has that kind of power under the hood. I'm not an expert, though, and information from somebo

...

///////////////////////////////////////////////////////////////
PS3 Problem is, there's a lot of great games out.  I love Ut3 on ps3 especially with keyboard and mouse...but there's so many great games, I rarely decide to play it.
///////////////////////////////////////////////////////////////
Steam i broke the bad habit of pirating a long time ago.  these days i just get the xbox360/ps3 version if a game uses unresonable drm.
///////////////////////////////////////////////////////////////
AskReddit 2 jtagged xbox360s I need to put back together and change their dvd keys. A ps3 I need to reflow and make two copper shims for. And an arduino programmer I need to figure out. 
///////////////////////////////////////////////////////////////
gaming the only other rpg esque game that i can think of for the ps3 is marvel ultimate alliance. not sure if that's what you're looking for though.
///////////////////////////////////////////////////////////////
AskReddit I bought a wireless logitech ps

///////////////////////////////////////////////////////////////
DoesAnybodyElse Whats tv? The thinge that I work with the xbox/ps3 ?
///////////////////////////////////////////////////////////////
badcompany2 I say hold out on PC for BF3, but join us in r/ps3bc2 on ps3. I understand you're put in alot of shitty lobbies when you get on the ps3, but if you can manage to play with a handful of us over in the ps3 subreddit, you're almost guaranteed a good time (unless you're on the opposite team of the redditors, then you'll smash your ps3)
///////////////////////////////////////////////////////////////
gaming I disagree, the framerate on the ps2 is lower but it's way more fixed and constant. On the PC it's sharper, clearer, and often way smoother, but I still prefer the PS2 version. The textures looked better and the motion blur was more fluid.

I tried it on the PC with a PS3 controller (using motioninjoy to emulate the ps3 controller with the highly compatible x360 controller drivers)
/


///////////////////////////////////////////////////////////////
gaming See if he cant make it any slower.

Mine got played three time by the kids boxed back up and out in the closet.
They fought so much over the ps3 we had to buy another.
///////////////////////////////////////////////////////////////
PS3 Google "red screen of epic fail". It's caused by attempting to roll back the firmware version for jailbreaking purposes. Norhing to do with the hdd. There might be a fix, not sure, the fact someone threw it in the bin doesn't bode well! Try a ps3 jailbreaking board. 
///////////////////////////////////////////////////////////////
gaming ~10 hour game. There's co-op too.

Chances are they're going to be releasing free content later down the road. And if not for some odd reason, the  there's all the custom content that will be coming eventually too.

It was like 35 if you pre-ordered, and many people have already been given it for free from valve because of potatoes and the ps3 deal.



gaming [Official PS Blog Link](http://blog.us.playstation.com/2011/04/26/update-on-playstation-network-and-qriocity/)
///////////////////////////////////////////////////////////////
gaming They released the [same statement](http://blog.eu.playstation.com/) on the European blog. 

[Here's a FAQ](http://faq.en.playstation.com/cgi-bin/scee_gb.cfg/php/enduser/std_adp.php?locale=en_GB&amp;p_faqid=5593) posted for those in the EU. 
///////////////////////////////////////////////////////////////
gaming Anteater, I don't believe so, as that information is sent independent of the PSN. If you notice you can still login to Netflix via ps3 even without PSN being up. Your information should be safe, but I'm ultimately just giving you and educated guess. 
///////////////////////////////////////////////////////////////
ps3bc2 I better read them 'cause I sure as hell die a LOT more when you're playing.  You're a vicious bastard and I mean that in the nicest way.

Do you play on PC also?  My experience

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [5]:
#convert lists of jsons to dataframe and export results
xbox_df = pd.DataFrame()
for post, year, month in xbox_json_list:
    s = pd.Series([post['id'], post['score'], post['controversiality'], post['subreddit'], post['body'], year, month])
    xbox_df = xbox_df.append(s, ignore_index = True)
print(xbox_df.head())

print()

ps_df = pd.DataFrame()
for post, year, month in ps_json_list:
    s = pd.Series([post['id'], post['score'], post['controversiality'], post['subreddit'], post['body'], year, month])
    ps_df = ps_df.append(s, ignore_index = True)
print(ps_df.head())

         0    1    2          3  \
0  c1b07tv  4.0  0.0      funny   
1  c1b08tv  1.0  0.0  AskReddit   
2  c1b09b6 -2.0  0.0  AskReddit   
3  c1b09ff  1.0  0.0  argentina   
4  c1b09u1  1.0  0.0  AskReddit   

                                                   4     5   6  
0  The problem with the happy medium is the quest...  2011  01  
1  When the xbox's are turned on and playing, tur...  2011  01  
2  Get the xbox. You buy the live, you buy the ga...  2011  01  
3  The only way you are going to get the xbox wor...  2011  01  
4  xbox is like free, ps3 is like 300 bucks, do t...  2011  01  

         0    1    2       3  \
0  c1b06r1  2.0  0.0  gaming   
1  c1b07cn  1.0  0.0   linux   
2  c1b07do  1.0  0.0     PS3   
3  c1b07hr  0.0  0.0  gaming   
4  c1b07zv  1.0  0.0  gaming   

                                                   4     5   6  
0  Just decided to give the series a try on the p...  2011  01  
1                                       xbmc on ps3?  2011  01  
2         

In [6]:
#clean up the dataframes
xbox_df.rename(columns = {0:'id', 1:'score', 2:'controversiality', 3:'subreddit', 4:'body', 5:'year', 6:'month'}, inplace = True)
ps_df.rename(columns = {0:'id', 1:'score', 2:'controversiality', 3:'subreddit', 4:'body', 5:'year', 6:'month'}, inplace = True)

xbox_df.set_index('id', inplace = True)
ps_df.set_index('id', inplace = True)
print(xbox_df.head())
print()
print(ps_df.head())

         score  controversiality  subreddit  \
id                                            
c1b07tv    4.0               0.0      funny   
c1b08tv    1.0               0.0  AskReddit   
c1b09b6   -2.0               0.0  AskReddit   
c1b09ff    1.0               0.0  argentina   
c1b09u1    1.0               0.0  AskReddit   

                                                      body  year month  
id                                                                      
c1b07tv  The problem with the happy medium is the quest...  2011    01  
c1b08tv  When the xbox's are turned on and playing, tur...  2011    01  
c1b09b6  Get the xbox. You buy the live, you buy the ga...  2011    01  
c1b09ff  The only way you are going to get the xbox wor...  2011    01  
c1b09u1  xbox is like free, ps3 is like 300 bucks, do t...  2011    01  

         score  controversiality subreddit  \
id                                           
c1b06r1    2.0               0.0    gaming   
c1b07cn    1.0      

In [7]:
#save dataframes as files for future use (done one year at a time, otherwise this needs to be in a loop)
xbox_df.to_json('dataframes/xbox_df'+years[0]+'.json', orient='columns')
ps_df.to_json('dataframes/ps_df'+years[0]+'.json', orient='columns')

df = pd.read_json('dataframes/xbox_df'+years[0]+'.json', orient='columns')
print(df.head())

df2 = pd.read_json('dataframes/ps_df'+years[0]+'.json', orient='columns')
print(df2.head())

         score  controversiality  subreddit  \
c1b07tv      4                 0      funny   
c1b08tv      1                 0  AskReddit   
c1b09b6     -2                 0  AskReddit   
c1b09ff      1                 0  argentina   
c1b09u1      1                 0  AskReddit   

                                                      body  year  month  
c1b07tv  The problem with the happy medium is the quest...  2011      1  
c1b08tv  When the xbox's are turned on and playing, tur...  2011      1  
c1b09b6  Get the xbox. You buy the live, you buy the ga...  2011      1  
c1b09ff  The only way you are going to get the xbox wor...  2011      1  
c1b09u1  xbox is like free, ps3 is like 300 bucks, do t...  2011      1  
         score  controversiality subreddit  \
c1b06r1      2                 0    gaming   
c1b07cn      1                 0     linux   
c1b07do      1                 0       PS3   
c1b07hr      0                 0    gaming   
c1b07zv      1                 0    gaming 